In [29]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from scipy import stats 
import plotly.express as px
import plotly.graph_objects as go
import nbformat
from sklearn.impute import SimpleImputer
from io import StringIO
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import SelectKBest, chi2
from imblearn.over_sampling import SMOTE
from sklearn.model_selection import train_test_split
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
from sklearn.naive_bayes import GaussianNB
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import LabelEncoder
from sklearn.feature_selection import SelectKBest, f_classif
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier



In [30]:
# Load the dataset (replace 'your_dataset.csv' with your actual dataset file)
df = pd.read_csv('Travel.csv')

In [31]:
# Display the first few rows of the dataset
print("First few rows of the dataset:")
df

First few rows of the dataset:


CustomerID  ProdTaken   Age    TypeofContact  CityTier  DurationOfPitch  \
0         200000          1  41.0     Self Enquiry         3              6.0   
1         200001          0  49.0  Company Invited         1             14.0   
2         200002          1  37.0     Self Enquiry         1              8.0   
3         200003          0  33.0  Company Invited         1              9.0   
4         200004          0   NaN     Self Enquiry         1              8.0   
...          ...        ...   ...              ...       ...              ...   
4883      204883          1  49.0     Self Enquiry         3              9.0   
4884      204884          1  28.0  Company Invited         1             31.0   
4885      204885          1  52.0     Self Enquiry         3             17.0   
4886      204886          1  19.0     Self Enquiry         3             16.0   
4887      204887          1  36.0     Self Enquiry         1             14.0   

          Occupation  Gender  NumberOfPersonVisiting  NumberOfFollowups  \
0           Salaried  Female                       3                3.0   
1           Salaried    Male                       3                4.0   
2        Free Lancer    Male                       3                4.0   
3           Salaried  Female                       2                3.0   
4     Small Business    Male                       2                3.0   
...              ...     ...                     ...                ...   
4883  Small Business    Male                       3                5.0   
4884        Salaried    Male                       4                5.0   
4885        Salaried  Female                       4                4.0   
4886  Small Business    Male                       3                4.0   
4887        Salaried    Male                       4                4.0   

     ProductPitched  PreferredPropertyStar MaritalStatus  NumberOfTrips  \
0            Deluxe                    3.0        Single            1.0   
1            Deluxe                    4.0      Divorced            2.0   
2             Basic                    3.0        Single            7.0   
3             Basic                    3.0      Divorced            2.0   
4             Basic                    4.0      Divorced            1.0   
...             ...                    ...           ...            ...   
4883         Deluxe                    4.0     Unmarried            2.0   
4884          Basic                    3.0        Single            3.0   
4885       Standard                    4.0       Married            7.0   
4886          Basic                    3.0        Single            3.0   
4887          Basic                    4.0     Unmarried            3.0   

      Passport  PitchSatisfactionScore  OwnCar  NumberOfChildrenVisiting  \
0            1                       2       1                       0.0   
1            0                       3       1                       2.0   
2            1                       3       0                       0.0   
3            1                       5       1                       1.0   
4            0                       5       1                       0.0   
...        ...                     ...     ...                       ...   
4883         1                       1       1                       1.0   
4884         1                       3       1                       2.0   
4885         0                       1       1                       3.0   
4886         0                       5       0                       2.0   
4887         1                       3       1                       2.0   

         Designation  MonthlyIncome  
0            Manager        20993.0  
1            Manager        20130.0  
2          Executive        17090.0  
3          Executive        17909.0  
4          Executive        18468.0  
...              ...            ...  
4883         Manager        26576.0  
4884       Exe

In [32]:
# Display the general information about the dataset
print("\nGeneral Information:")
print(df.info())


General Information:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4888 entries, 0 to 4887
Data columns (total 20 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   CustomerID                4888 non-null   int64  
 1   ProdTaken                 4888 non-null   int64  
 2   Age                       4662 non-null   float64
 3   TypeofContact             4863 non-null   object 
 4   CityTier                  4888 non-null   int64  
 5   DurationOfPitch           4637 non-null   float64
 6   Occupation                4888 non-null   object 
 7   Gender                    4888 non-null   object 
 8   NumberOfPersonVisiting    4888 non-null   int64  
 9   NumberOfFollowups         4843 non-null   float64
 10  ProductPitched            4888 non-null   object 
 11  PreferredPropertyStar     4862 non-null   float64
 12  MaritalStatus             4888 non-null   object 
 13  NumberOfTrips             4748 non-null  

In [33]:
# Descriptive statistics for numerical columns
numerical_stats = df.describe()

# Descriptive statistics for categorical columns
categorical_stats = pd.DataFrame()
for col in df.select_dtypes(include=['object', 'category']):
    categorical_stats[col] = [df[col].nunique(),
                              df[col].value_counts().idxmax(),
                              df[col].value_counts().max() / len(df) * 100]

categorical_stats = categorical_stats.rename(columns={0: 'Unique Categories', 1: 'Most Common Category', 2: 'Percentage'})

# Print descriptive statistics
print("Descriptive Statistics for Numerical Columns:")
print(numerical_stats)
print("\nDescriptive Statistics for Categorical Columns:")
print(categorical_stats)


Descriptive Statistics for Numerical Columns:
          CustomerID    ProdTaken          Age     CityTier  DurationOfPitch  \
count    4888.000000  4888.000000  4662.000000  4888.000000      4637.000000   
mean   202443.500000     0.188216    37.622265     1.654255        15.490835   
std      1411.188388     0.390925     9.316387     0.916583         8.519643   
min    200000.000000     0.000000    18.000000     1.000000         5.000000   
25%    201221.750000     0.000000    31.000000     1.000000         9.000000   
50%    202443.500000     0.000000    36.000000     1.000000        13.000000   
75%    203665.250000     0.000000    44.000000     3.000000        20.000000   
max    204887.000000     1.000000    61.000000     3.000000       127.000000   

       NumberOfPersonVisiting  NumberOfFollowups  PreferredPropertyStar  \
count             4888.000000        4843.000000            4862.000000   
mean                 2.905074           3.708445               3.581037   
std     

In [34]:
# Check data types
print("\nData Types:")
print(df.dtypes)


Data Types:
CustomerID                    int64
ProdTaken                     int64
Age                         float64
TypeofContact                object
CityTier                      int64
DurationOfPitch             float64
Occupation                   object
Gender                       object
NumberOfPersonVisiting        int64
NumberOfFollowups           float64
ProductPitched               object
PreferredPropertyStar       float64
MaritalStatus                object
NumberOfTrips               float64
Passport                      int64
PitchSatisfactionScore        int64
OwnCar                        int64
NumberOfChildrenVisiting    float64
Designation                  object
MonthlyIncome               float64
dtype: object


In [35]:

# Assuming 'df' is your DataFrame containing the data

# Distribution of Age
fig1 = px.histogram(df, x='Age', nbins=10, title='Distribution of Age', marginal='box', hover_data=df.columns)
fig1.show()

# Pie Chart of Product Taken
fig2 = px.pie(df, names='ProdTaken', title='Distribution of Product Taken')
fig2.show()

# Boxplot of Monthly Income by Gender
fig3 = px.box(df, x='Gender', y='MonthlyIncome', title='Monthly Income by Gender', points='all')
fig3.show()

# Barplot of Product Pitched by Number of Followups
fig4 = px.bar(df, x='NumberOfFollowups', y='ProdTaken', color='ProductPitched', barmode='group',
              title='Product Pitched by Number of Followups')
fig4.show()

# Heatmap of correlation matrix
numeric_columns = df.select_dtypes(include=['number']).columns
correlation_matrix = df[numeric_columns].corr()

fig5 = go.Figure(data=go.Heatmap(
                   z=correlation_matrix.values,
                   x=correlation_matrix.columns,
                   y=correlation_matrix.columns,
                   colorscale='Viridis'))

fig5.update_layout(title='Correlation Matrix')
fig5.show()

# Scatter Plot of Age vs Monthly Income by Gender
fig6 = px.scatter(df, x='Age', y='MonthlyIncome', color='Gender',
                  title='Age vs Monthly Income by Gender',
                  hover_data=['Designation', 'CityTier'])
fig6.show()

# Pie Chart of Marital Status Distribution
fig7 = px.pie(df, names='MaritalStatus', title='Marital Status Distribution')
fig7.show()

# Sunburst Chart for Multi-level Hierarchical Data (CityTier -> Gender -> ProductPitched)
fig8 = px.sunburst(df, path=['CityTier', 'Gender', 'ProductPitched'],
                   values='CustomerID', title='Sunburst Chart of CityTier, Gender and Product Pitched')
fig8.show()

# Violin Plot of Monthly Income by Designation
fig9 = px.violin(df, x='Designation', y='MonthlyIncome',
                 title='Monthly Income by Designation',
                 box=True, points='all')
fig9.show()

# Grouped Bar Plot for Number of Trips vs Age by Product Taken
fig10_alternative = px.bar(df, x='Age', y='NumberOfTrips', color='ProdTaken',
                            title='Number of Trips vs Age by Product Taken',
                            barmode='group', hover_data=['CustomerID'])
fig10_alternative.show()

# Scatter Plot of Age vs Duration of Pitch colored by Gender
fig11_alternative = px.scatter(df, x='Age', y='DurationOfPitch', color='Gender',
                               title='Age vs Duration of Pitch by Gender',
                               hover_data=['CustomerID'])
fig11_alternative.show()



In [36]:
import nbformat
print(nbformat.__version__)


5.10.4


In [37]:
# Identify missing values
missing_values = df.isna().sum()
print("Missing Values:")
print(missing_values)

Missing Values:
CustomerID                    0
ProdTaken                     0
Age                         226
TypeofContact                25
CityTier                      0
DurationOfPitch             251
Occupation                    0
Gender                        0
NumberOfPersonVisiting        0
NumberOfFollowups            45
ProductPitched                0
PreferredPropertyStar        26
MaritalStatus                 0
NumberOfTrips               140
Passport                      0
PitchSatisfactionScore        0
OwnCar                        0
NumberOfChildrenVisiting     66
Designation                   0
MonthlyIncome               233
dtype: int64


In [38]:

# Replace 'Fe Male' with 'Female'
df['Gender'] = df['Gender'].replace('Fe Male', 'Female')

# Imputation code
numerical_cols = ['Age', 'DurationOfPitch', 'NumberOfFollowups', 'NumberOfTrips', 'MonthlyIncome','NumberOfChildrenVisiting']
categorical_cols = ['TypeofContact', 'PreferredPropertyStar']

# Handling missing values for numerical columns using mean imputation
imputer_mean = SimpleImputer(strategy='mean')
df[numerical_cols] = imputer_mean.fit_transform(df[numerical_cols])

# Handling missing values for categorical columns using mode imputation
imputer_mode = SimpleImputer(strategy='most_frequent')
df[categorical_cols] = imputer_mode.fit_transform(df[categorical_cols])


# Check if there are any remaining missing values
print("Remaining missing values:")
print(df.isnull().sum())

# Save the cleaned dataset
df.to_csv('cleaned_dataset.csv', index=False)
print("Cleaned data saved to 'cleaned_dataset.csv'")


Remaining missing values:
CustomerID                  0
ProdTaken                   0
Age                         0
TypeofContact               0
CityTier                    0
DurationOfPitch             0
Occupation                  0
Gender                      0
NumberOfPersonVisiting      0
NumberOfFollowups           0
ProductPitched              0
PreferredPropertyStar       0
MaritalStatus               0
NumberOfTrips               0
Passport                    0
PitchSatisfactionScore      0
OwnCar                      0
NumberOfChildrenVisiting    0
Designation                 0
MonthlyIncome               0
dtype: int64
Cleaned data saved to 'cleaned_dataset.csv'


In [39]:
df1=pd.read_csv('cleaned_dataset.csv')

In [40]:

# Label Encoding for categorical variables
label_encoder = LabelEncoder()

df1['TypeofContact'] = label_encoder.fit_transform(df1['TypeofContact'])
df1['Occupation'] = label_encoder.fit_transform(df1['Occupation'])
df1['Gender'] = label_encoder.fit_transform(df1['Gender'])
df1['ProductPitched'] = label_encoder.fit_transform(df1['ProductPitched'])
df1['MaritalStatus'] = label_encoder.fit_transform(df1['MaritalStatus'])
df1['Designation'] = label_encoder.fit_transform(df1['Designation'])
print(df1)

      CustomerID  ProdTaken        Age  TypeofContact  CityTier  \
0         200000          1  41.000000              1         3   
1         200001          0  49.000000              0         1   
2         200002          1  37.000000              1         1   
3         200003          0  33.000000              0         1   
4         200004          0  37.622265              1         1   
...          ...        ...        ...            ...       ...   
4883      204883          1  49.000000              1         3   
4884      204884          1  28.000000              0         1   
4885      204885          1  52.000000              1         3   
4886      204886          1  19.000000              1         3   
4887      204887          1  36.000000              1         1   

      DurationOfPitch  Occupation  Gender  NumberOfPersonVisiting  \
0                 6.0           2       0                       3   
1                14.0           2       1                

Feature Selection:(Random Forest,Chi2,ANOVA)

In [41]:

# Define the features and target variable
X = df1.drop(columns=['ProdTaken'])
y = df1['ProdTaken']

# Train a Random Forest Classifier
clf = RandomForestClassifier(n_estimators=100, random_state=42)
clf.fit(X, y)

# Get feature importances
importances = clf.feature_importances_
feature_names = X.columns

# Create a DataFrame for visualization
feature_importances = pd.DataFrame({
    'Feature': feature_names,
    'Importance': importances
}).sort_values(by='Importance', ascending=False)

# Select top 10 features
top_features_rf = feature_importances.head(10)['Feature'].values

# Print top features
print("Top 10 features:", top_features_rf)

# Update the feature set with the selected top features
X_selected = X[top_features_rf]

Top 10 features: ['Age' 'CustomerID' 'MonthlyIncome' 'DurationOfPitch' 'Passport'
 'NumberOfTrips' 'PitchSatisfactionScore' 'MaritalStatus'
 'NumberOfFollowups' 'ProductPitched']


In [42]:

# Use chi2 to select top features
selector = SelectKBest(score_func=chi2, k=10)
X_selected = selector.fit_transform(X, y)

# Get selected feature indices
selected_indices = selector.get_support(indices=True)

# Get selected feature names
selected_features_chi2 = X.columns[selected_indices]

# Print selected features
print("Selected Features:")
for feature_chi2 in selected_features_chi2:
    print(feature_chi2)


Selected Features:
CustomerID
Age
CityTier
DurationOfPitch
NumberOfFollowups
ProductPitched
MaritalStatus
Passport
Designation
MonthlyIncome


In [43]:

# Assuming df1 is already defined and preprocessed

# Use ANOVA to select top features
selector = SelectKBest(score_func=f_classif, k=10)
X_selected = selector.fit_transform(X, y)

# Get selected feature indices
selected_indices = selector.get_support(indices=True)

# Get selected feature names
selected_features_anova = X.columns[selected_indices]

# Print selected features
print("Selected Features:")
for feature_anova in selected_features_anova:
    print(feature_anova)


Selected Features:
Age
CityTier
DurationOfPitch
NumberOfFollowups
ProductPitched
PreferredPropertyStar
MaritalStatus
Passport
Designation
MonthlyIncome


In [44]:
# Find intersection of the top features from all three methods
common_features = list(set(top_features_rf) & set(selected_features_chi2) & set(selected_features_anova) )
print("Common features selected by Random Forest, Chi-Square, and ANOVA:", common_features)

Common features selected by Random Forest, Chi-Square, and ANOVA: ['MaritalStatus', 'MonthlyIncome', 'Passport', 'DurationOfPitch', 'ProductPitched', 'Age', 'NumberOfFollowups']


In [45]:
# Filter the dataset using the common features
X_common = X[common_features]

# Split the data into training and testing sets using the common features
X_train_common, X_test_common, y_train, y_test = train_test_split(X_common, y, test_size=0.3, random_state=42)
# Print the shapes of the training and testing sets
print("Shape of X_train_common:", X_train_common.shape)
print("Shape of X_test_common:", X_test_common.shape)
print("Shape of y_train:", y_train.shape)
print("Shape of y_test:", y_test.shape)

Shape of X_train_common: (3421, 7)
Shape of X_test_common: (1467, 7)
Shape of y_train: (3421,)
Shape of y_test: (1467,)


In [46]:
# Assuming you have already filtered the dataset and split into train/test
X_common = X[common_features]
X_train_common, X_test_common, y_train, y_test = train_test_split(X_common, y, test_size=0.3, random_state=42)

# Apply SMOTE to the training data
smote = SMOTE(random_state=42)
X_train_smote, y_train_smote = smote.fit_resample(X_train_common, y_train)

# Print the shapes of the new training sets
print("Shape of X_train_smote:", X_train_smote.shape)
print("Shape of y_train_smote:", y_train_smote.shape)

# Check the value counts after SMOTE
print("Value counts for y_train_smote:")
print(y_train_smote.value_counts())


Shape of X_train_smote: (5550, 7)
Shape of y_train_smote: (5550,)
Value counts for y_train_smote:
ProdTaken
0    2775
1    2775
Name: count, dtype: int64


In [47]:

# Initialize the StandardScaler
scaler = StandardScaler()

# Fit the scaler on the training data and transform the training data
X_train_scaled = scaler.fit_transform(X_train_smote)

# Transform the testing data using the fitted scaler
X_test_scaled = scaler.transform(X_test_common)

# Print the shapes of the scaled training and testing sets
print("Shape of X_train_scaled:", X_train_scaled.shape)
print("Shape of X_test_scaled:", X_test_scaled.shape)


Shape of X_train_scaled: (5550, 7)
Shape of X_test_scaled: (1467, 7)


naive bayes


In [48]:

# Initialize the Naive Bayes classifier
nb_clf = GaussianNB()

# Train the classifier
nb_clf.fit(X_train_scaled, y_train_smote)

# Make predictions on the training set
y_train_pred_nb = nb_clf.predict(X_train_scaled)

# Make predictions on the testing set
y_test_pred_nb = nb_clf.predict(X_test_scaled)

# Calculate the training accuracy
accuracy_train_nb = accuracy_score(y_train_smote, y_train_pred_nb)

# Evaluate the classifier on the testing set
accuracy_test_nb = accuracy_score(y_test, y_test_pred_nb)

# Generate classification reports
report_train_nb = classification_report(y_train_smote, y_train_pred_nb)
report_test_nb = classification_report(y_test, y_test_pred_nb)

# Print results
print(f"Naive Bayes Training Accuracy: {accuracy_train_nb}")
print("Naive Bayes Training Classification Report:")
print(report_train_nb)

print(f"Naive Bayes Testing Accuracy: {accuracy_test_nb}")
print("Naive Bayes Testing Classification Report:")
print(report_test_nb)

print("Naive Bayes Testing Confusion Matrix:")
print(confusion_matrix(y_test, y_test_pred_nb))


Naive Bayes Training Accuracy: 0.6091891891891892
Naive Bayes Training Classification Report:
              precision    recall  f1-score   support

           0       0.65      0.48      0.55      2775
           1       0.59      0.74      0.65      2775

    accuracy                           0.61      5550
   macro avg       0.62      0.61      0.60      5550
weighted avg       0.62      0.61      0.60      5550

Naive Bayes Testing Accuracy: 0.5351056578050443
Naive Bayes Testing Classification Report:
              precision    recall  f1-score   support

           0       0.89      0.49      0.63      1193
           1       0.25      0.73      0.37       274

    accuracy                           0.54      1467
   macro avg       0.57      0.61      0.50      1467
weighted avg       0.77      0.54      0.58      1467

Naive Bayes Testing Confusion Matrix:
[[585 608]
 [ 74 200]]


Tuned NB model 

In [49]:

# Initialize the Naive Bayes classifier
nb_clf = GaussianNB()

# Set up the parameter grid
param_grid = {
    'var_smoothing': [1e-9, 1e-8, 1e-7, 1e-6, 1e-5, 1e-4, 1e-3, 1e-2, 1e-1, 1]
}

# Initialize GridSearchCV
grid_search = GridSearchCV(estimator=nb_clf, param_grid=param_grid, cv=5, scoring='accuracy', n_jobs=-1)

# Fit GridSearchCV
grid_search.fit(X_train_scaled, y_train_smote)

# Get the best parameters and the best estimator
best_params = grid_search.best_params_
best_nb_clf = grid_search.best_estimator_

print(f"Best parameters found: {best_params}")

# Train the best estimator
best_nb_clf.fit(X_train_scaled, y_train_smote)

# Make predictions on the training set
y_train_pred_nb = best_nb_clf.predict(X_train_scaled)

# Make predictions on the testing set
y_test_pred_nb = best_nb_clf.predict(X_test_scaled)

# Calculate the training accuracy
accuracy_train_at_nb = accuracy_score(y_train_smote, y_train_pred_nb)

# Evaluate the classifier on the testing set
accuracy_test_at_nb = accuracy_score(y_test, y_test_pred_nb)

# Generate classification reports
report_train_at_nb = classification_report(y_train_smote, y_train_pred_nb)
report_test_at_nb = classification_report(y_test, y_test_pred_nb)

# Print results
print(f"Naive Bayes Training Accuracy: {accuracy_train_at_nb}")
print("Naive Bayes Training Classification Report:")
print(report_train_at_nb)

print(f"Naive Bayes Testing Accuracy: {accuracy_test_at_nb}")
print("Naive Bayes Testing Classification Report:")
print(report_test_at_nb)




Best parameters found: {'var_smoothing': 0.01}
Naive Bayes Training Accuracy: 0.6086486486486486
Naive Bayes Training Classification Report:
              precision    recall  f1-score   support

           0       0.65      0.48      0.55      2775
           1       0.59      0.74      0.65      2775

    accuracy                           0.61      5550
   macro avg       0.62      0.61      0.60      5550
weighted avg       0.62      0.61      0.60      5550

Naive Bayes Testing Accuracy: 0.534423994546694
Naive Bayes Testing Classification Report:
              precision    recall  f1-score   support

           0       0.89      0.49      0.63      1193
           1       0.25      0.73      0.37       274

    accuracy                           0.53      1467
   macro avg       0.57      0.61      0.50      1467
weighted avg       0.77      0.53      0.58      1467



GBM

In [50]:

# Initialize the GBM classifier
gbm_clf = GradientBoostingClassifier(n_estimators=100, learning_rate=0.1, max_depth=3, random_state=42)

# Train the classifier on the SMOTE variables
gbm_clf.fit(X_train_scaled, y_train_smote)

# Make predictions on the training set
y_train_pred_gbm = gbm_clf.predict(X_train_scaled)

# Make predictions on the testing set
y_test_pred_gbm = gbm_clf.predict(X_test_scaled)

# Calculate the training accuracy
accuracy_train_gbm = accuracy_score(y_train_smote, y_train_pred_gbm)

# Evaluate the classifier on the testing set
accuracy_test_gbm = accuracy_score(y_test, y_test_pred_gbm)

# Generate classification reports
report_train_gbm = classification_report(y_train_smote, y_train_pred_gbm)
report_test_gbm = classification_report(y_test, y_test_pred_gbm)

# Print results
print(f"GBM Training Accuracy: {accuracy_train_gbm}")
print("GBM Training Classification Report:")
print(report_train_gbm)

print(f"GBM Testing Accuracy: {accuracy_test_gbm}")
print("GBM Testing Classification Report:")
print(report_test_gbm)

print("GBM Testing Confusion Matrix:")
print(confusion_matrix(y_test, y_test_pred_gbm))


GBM Training Accuracy: 0.849009009009009
GBM Training Classification Report:
              precision    recall  f1-score   support

           0       0.82      0.89      0.86      2775
           1       0.88      0.81      0.84      2775

    accuracy                           0.85      5550
   macro avg       0.85      0.85      0.85      5550
weighted avg       0.85      0.85      0.85      5550

GBM Testing Accuracy: 0.8077709611451943
GBM Testing Classification Report:
              precision    recall  f1-score   support

           0       0.89      0.87      0.88      1193
           1       0.49      0.55      0.52       274

    accuracy                           0.81      1467
   macro avg       0.69      0.71      0.70      1467
weighted avg       0.82      0.81      0.81      1467

GBM Testing Confusion Matrix:
[[1035  158]
 [ 124  150]]


Tuned GBM model

In [51]:

# Initialize the GBM classifier with default parameters
gbm_clf = GradientBoostingClassifier(random_state=42)

# Set up the parameter grid
param_grid = {
    'n_estimators': [100, 200, 300],
    'learning_rate': [0.01, 0.1, 0.2],
    'max_depth': [3, 4, 5],
    'subsample': [0.8, 0.9, 1.0],
    'max_features': ['sqrt', 'log2', None]
}

# Initialize GridSearchCV
grid_search = GridSearchCV(estimator=gbm_clf, param_grid=param_grid, cv=5, scoring='accuracy', n_jobs=-1)

# Fit GridSearchCV
grid_search.fit(X_train_scaled, y_train_smote)

# Get the best parameters and the best estimator
best_params = grid_search.best_params_
gbm_clf = grid_search.best_estimator_

print(f"Best parameters found: {best_params}")
best_gbm_clf = GradientBoostingClassifier(**best_params, random_state=42)

# Train the best estimator
best_gbm_clf.fit(X_train_scaled, y_train_smote)

# Make predictions on the training set
y_train_pred_gbm = best_gbm_clf.predict(X_train_scaled)

# Make predictions on the testing set
y_test_pred_gbm = best_gbm_clf.predict(X_test_scaled)

# Calculate the training accuracy
accuracy_train_at_gbm = accuracy_score(y_train_smote, y_train_pred_gbm)

# Evaluate the classifier on the testing set
accuracy_test_at_gbm = accuracy_score(y_test, y_test_pred_gbm)

# Generate classification reports
report_train_at_gbm = classification_report(y_train_smote, y_train_pred_gbm)
report_test_at_gbm = classification_report(y_test, y_test_pred_gbm)

# Print results
print(f"GBM Training Accuracy: {accuracy_train_at_gbm}")
print("GBM Training Classification Report:")
print(report_train_at_gbm)

print(f"GBM Testing Accuracy: {accuracy_test_at_gbm}")
print("GBM Testing Classification Report:")
print(report_test_at_gbm)

print("GBM Testing Confusion Matrix:")
print(confusion_matrix(y_test, y_test_pred_gbm))


Best parameters found: {'learning_rate': 0.2, 'max_depth': 5, 'max_features': None, 'n_estimators': 300, 'subsample': 1.0}
GBM Training Accuracy: 0.9978378378378379
GBM Training Classification Report:
              precision    recall  f1-score   support

           0       1.00      1.00      1.00      2775
           1       1.00      1.00      1.00      2775

    accuracy                           1.00      5550
   macro avg       1.00      1.00      1.00      5550
weighted avg       1.00      1.00      1.00      5550

GBM Testing Accuracy: 0.9032038173142468
GBM Testing Classification Report:
              precision    recall  f1-score   support

           0       0.92      0.96      0.94      1193
           1       0.80      0.64      0.71       274

    accuracy                           0.90      1467
   macro avg       0.86      0.80      0.83      1467
weighted avg       0.90      0.90      0.90      1467

GBM Testing Confusion Matrix:
[[1149   44]
 [  98  176]]


Random Forest

In [52]:

# Initialize the Random Forest classifier
rf_clf = RandomForestClassifier(n_estimators=100, random_state=42)

# Train the classifier on the SMOTE variables
rf_clf.fit(X_train_scaled, y_train_smote)

# Make predictions on the training set
y_train_pred_rf = rf_clf.predict(X_train_scaled)

# Make predictions on the testing set
y_test_pred_rf = rf_clf.predict(X_test_scaled)

# Calculate the training accuracy
accuracy_train_rf = accuracy_score(y_train_smote, y_train_pred_rf)

# Evaluate the classifier on the testing set
accuracy_test_rf = accuracy_score(y_test, y_test_pred_rf)

# Generate classification reports
report_train_rf = classification_report(y_train_smote, y_train_pred_rf)
report_test_rf = classification_report(y_test, y_test_pred_rf)

# Print results
print(f"Random Forest Training Accuracy: {accuracy_train_rf}")
print("Random Forest Training Classification Report:")
print(report_train_rf)

print(f"Random Forest Testing Accuracy: {accuracy_test_rf}")
print("Random Forest Testing Classification Report:")
print(report_test_rf)

print("Random Forest Testing Confusion Matrix:")
print(confusion_matrix(y_test, y_test_pred_rf))


Random Forest Training Accuracy: 0.9992792792792793
Random Forest Training Classification Report:
              precision    recall  f1-score   support

           0       1.00      1.00      1.00      2775
           1       1.00      1.00      1.00      2775

    accuracy                           1.00      5550
   macro avg       1.00      1.00      1.00      5550
weighted avg       1.00      1.00      1.00      5550

Random Forest Testing Accuracy: 0.8984321745057942
Random Forest Testing Classification Report:
              precision    recall  f1-score   support

           0       0.92      0.96      0.94      1193
           1       0.78      0.64      0.70       274

    accuracy                           0.90      1467
   macro avg       0.85      0.80      0.82      1467
weighted avg       0.89      0.90      0.89      1467

Random Forest Testing Confusion Matrix:
[[1143   50]
 [  99  175]]


Tuned rf model

In [53]:

# Define the parameter grid
param_grid = {
    'n_estimators': [100, 200, 300],
    'max_depth': [None, 10, 20, 30],
    'min_samples_split': [2, 5, 10],
    'min_samples_leaf': [1, 2, 4],
    'bootstrap': [True, False]
}

# Initialize the Random Forest classifier
rf_clf = RandomForestClassifier(random_state=42)

# Initialize GridSearchCV
grid_search = GridSearchCV(estimator=rf_clf, param_grid=param_grid, cv=5, scoring='accuracy', n_jobs=-1, verbose=2)

# Fit GridSearchCV
grid_search.fit(X_train_scaled, y_train_smote)

# Get the best parameters and the best estimator
best_params = grid_search.best_params_
best_rf_clf = grid_search.best_estimator_

print(f"Best parameters found: {best_params}")

# Train the best estimator
best_rf_clf.fit(X_train_scaled, y_train_smote)

# Make predictions on the training set
y_train_at_pred_rf = best_rf_clf.predict(X_train_scaled)

# Make predictions on the testing set
y_test_at_pred_rf = best_rf_clf.predict(X_test_scaled)

# Calculate the training accuracy
accuracy_train_at_rf = accuracy_score(y_train_smote, y_train_at_pred_rf)

# Evaluate the classifier on the testing set
accuracy_test_at_rf = accuracy_score(y_test, y_test_at_pred_rf)

# Generate classification reports
report_train_at_rf = classification_report(y_train_smote, y_train_at_pred_rf)
report_test_at_rf = classification_report(y_test, y_test_at_pred_rf)

# Print results
print(f"Random Forest Training Accuracy: {accuracy_train_at_rf}")
print("Random Forest Training Classification Report:")
print(report_train_at_rf)

print(f"Random Forest Testing Accuracy: {accuracy_test_at_rf}")
print("Random Forest Testing Classification Report:")
print(report_test_at_rf)

print("Random Forest Testing Confusion Matrix:")
print(confusion_matrix(y_test, y_test_at_pred_rf))


Fitting 5 folds for each of 216 candidates, totalling 1080 fits
Best parameters found: {'bootstrap': True, 'max_depth': None, 'min_samples_leaf': 1, 'min_samples_split': 2, 'n_estimators': 100}
Random Forest Training Accuracy: 0.9992792792792793
Random Forest Training Classification Report:
              precision    recall  f1-score   support

           0       1.00      1.00      1.00      2775
           1       1.00      1.00      1.00      2775

    accuracy                           1.00      5550
   macro avg       1.00      1.00      1.00      5550
weighted avg       1.00      1.00      1.00      5550

Random Forest Testing Accuracy: 0.8984321745057942
Random Forest Testing Classification Report:
              precision    recall  f1-score   support

           0       0.92      0.96      0.94      1193
           1       0.78      0.64      0.70       274

    accuracy                           0.90      1467
   macro avg       0.85      0.80      0.82      1467
weighted avg 

KNN

In [54]:

# Initialize the KNN classifier
knn_clf = KNeighborsClassifier(n_neighbors=5)  # You can adjust the number of neighbors (n_neighbors) as needed

# Train the classifier on the SMOTE variables
knn_clf.fit(X_train_scaled, y_train_smote)

# Make predictions on the training set
y_train_pred_knn = knn_clf.predict(X_train_scaled)

# Make predictions on the testing set
y_test_pred_knn = knn_clf.predict(X_test_scaled)

# Calculate the training accuracy
accuracy_train_knn = accuracy_score(y_train_smote, y_train_pred_knn)

# Evaluate the classifier on the testing set
accuracy_test_knn = accuracy_score(y_test, y_test_pred_knn)

# Generate classification reports
report_train_knn = classification_report(y_train_smote, y_train_pred_knn)
report_test_knn = classification_report(y_test, y_test_pred_knn)

# Print results
print(f"K-Nearest Neighbors (KNN) Training Accuracy: {accuracy_train_knn}")
print("K-Nearest Neighbors (KNN) Training Classification Report:")
print(report_train_knn)

print(f"K-Nearest Neighbors (KNN) Testing Accuracy: {accuracy_test_knn}")
print("K-Nearest Neighbors (KNN) Testing Classification Report:")
print(report_test_knn)

print("K-Nearest Neighbors (KNN) Testing Confusion Matrix:")
print(confusion_matrix(y_test, y_test_pred_knn))


K-Nearest Neighbors (KNN) Training Accuracy: 0.8502702702702702
K-Nearest Neighbors (KNN) Training Classification Report:
              precision    recall  f1-score   support

           0       0.86      0.83      0.85      2775
           1       0.84      0.87      0.85      2775

    accuracy                           0.85      5550
   macro avg       0.85      0.85      0.85      5550
weighted avg       0.85      0.85      0.85      5550

K-Nearest Neighbors (KNN) Testing Accuracy: 0.7464212678936605
K-Nearest Neighbors (KNN) Testing Classification Report:
              precision    recall  f1-score   support

           0       0.90      0.78      0.83      1193
           1       0.39      0.62      0.48       274

    accuracy                           0.75      1467
   macro avg       0.64      0.70      0.65      1467
weighted avg       0.80      0.75      0.77      1467

K-Nearest Neighbors (KNN) Testing Confusion Matrix:
[[926 267]
 [105 169]]


Tuned KNN model

In [55]:

# Define the parameter grid
param_grid = {
    'n_neighbors': [3, 5, 7, 9, 11],
    'weights': ['uniform', 'distance'],
    'metric': ['euclidean', 'manhattan', 'minkowski']
}

# Initialize the KNN classifier
knn_clf = KNeighborsClassifier()

# Initialize GridSearchCV
grid_search = GridSearchCV(estimator=knn_clf, param_grid=param_grid, cv=5, scoring='accuracy', n_jobs=-1, verbose=2)

# Fit GridSearchCV
grid_search.fit(X_train_scaled, y_train_smote)

# Get the best parameters and the best estimator
best_params = grid_search.best_params_
best_knn_clf = grid_search.best_estimator_

print(f"Best parameters found: {best_params}")

# Train the best estimator
best_knn_clf.fit(X_train_scaled, y_train_smote)

# Make predictions on the training set
y_train_pred_knn = best_knn_clf.predict(X_train_scaled)

# Make predictions on the testing set
y_test_pred_knn = best_knn_clf.predict(X_test_scaled)

# Calculate the training accuracy
accuracy_train_knn = accuracy_score(y_train_smote, y_train_pred_knn)

# Evaluate the classifier on the testing set
accuracy_test_knn = accuracy_score(y_test, y_test_pred_knn)

# Generate classification reports
report_train_knn = classification_report(y_train_smote, y_train_pred_knn)
report_test_knn = classification_report(y_test, y_test_pred_knn)

# Print results
print(f"K-Nearest Neighbors (KNN) Training Accuracy: {accuracy_train_knn}")
print("K-Nearest Neighbors (KNN) Training Classification Report:")
print(report_train_knn)

print(f"K-Nearest Neighbors (KNN) Testing Accuracy: {accuracy_test_knn}")
print("K-Nearest Neighbors (KNN) Testing Classification Report:")
print(report_test_knn)

print("K-Nearest Neighbors (KNN) Testing Confusion Matrix:")
print(confusion_matrix(y_test, y_test_pred_knn))


Fitting 5 folds for each of 30 candidates, totalling 150 fits
Best parameters found: {'metric': 'manhattan', 'n_neighbors': 3, 'weights': 'distance'}
K-Nearest Neighbors (KNN) Training Accuracy: 0.9992792792792793
K-Nearest Neighbors (KNN) Training Classification Report:
              precision    recall  f1-score   support

           0       1.00      1.00      1.00      2775
           1       1.00      1.00      1.00      2775

    accuracy                           1.00      5550
   macro avg       1.00      1.00      1.00      5550
weighted avg       1.00      1.00      1.00      5550

K-Nearest Neighbors (KNN) Testing Accuracy: 0.8282208588957055
K-Nearest Neighbors (KNN) Testing Classification Report:
              precision    recall  f1-score   support

           0       0.92      0.87      0.89      1193
           1       0.53      0.66      0.59       274

    accuracy                           0.83      1467
   macro avg       0.73      0.77      0.74      1467
weighted 

RESULT

In [56]:
# Test accuracies before tuning
accuracy_test_before_tuning = {
    'Naive Bayes': accuracy_score(y_test, y_test_pred_nb),
    'Gradient Boosting': accuracy_score(y_test, y_test_pred_gbm),
    'Random Forest': accuracy_score(y_test, y_test_pred_rf),
    'K-Nearest Neighbors': accuracy_score(y_test, y_test_pred_knn)
}

# Test accuracies after tuning
accuracy_test_after_tuning = {
    'Naive Bayes': accuracy_score(y_test, y_test_pred_nb),
    'Gradient Boosting': accuracy_score(y_test, y_test_pred_gbm),
    'Random Forest': accuracy_score(y_test, y_test_pred_rf),
    'K-Nearest Neighbors': accuracy_score(y_test, y_test_pred_knn)
}

# Print test accuracies
print("Test Accuracies Before Tuning:")
for clf, accuracy in accuracy_test_before_tuning.items():
    print(f"{clf}: {accuracy}")

print("\nTest Accuracies After Tuning:")
for clf, accuracy in accuracy_test_after_tuning.items():
    print(f"{clf}: {accuracy}")

# Find the classifier with the maximum accuracy after tuning
max_accuracy_clf = max(accuracy_test_after_tuning, key=accuracy_test_after_tuning.get)
max_accuracy = accuracy_test_after_tuning[max_accuracy_clf]

print(f"\nThe classifier with the maximum accuracy after tuning is: {max_accuracy_clf} with accuracy: {max_accuracy}")


Test Accuracies Before Tuning:
Naive Bayes: 0.534423994546694
Gradient Boosting: 0.9032038173142468
Random Forest: 0.8984321745057942
K-Nearest Neighbors: 0.8282208588957055

Test Accuracies After Tuning:
Naive Bayes: 0.534423994546694
Gradient Boosting: 0.9032038173142468
Random Forest: 0.8984321745057942
K-Nearest Neighbors: 0.8282208588957055

The classifier with the maximum accuracy after tuning is: Gradient Boosting with accuracy: 0.9032038173142468


In [57]:
import pandas as pd

# Define empty lists to store metrics
classifiers = ['Naive Bayes', 'Gradient Boosting', 'Random Forest', 'K-Nearest Neighbors']
precision_before_tuning = []
recall_before_tuning = []
f1_score_before_tuning = []
accuracy_before_tuning = []

# Calculate metrics for each classifier
for clf, y_pred in zip([nb_clf, gbm_clf, rf_clf, knn_clf], [y_test_pred_nb, y_test_pred_gbm, y_test_pred_rf, y_test_pred_knn]):
    report = classification_report(y_test, y_pred, output_dict=True)
    precision_before_tuning.append(report['macro avg']['precision'])
    recall_before_tuning.append(report['macro avg']['recall'])
    f1_score_before_tuning.append(report['macro avg']['f1-score'])
    accuracy_before_tuning.append(report['accuracy'])

# Create a DataFrame to display the metrics
metrics_df = pd.DataFrame({
    'Classifier': classifiers,
    'Precision': precision_before_tuning,
    'Recall': recall_before_tuning,
    'F1 Score': f1_score_before_tuning,
    'Accuracy': accuracy_before_tuning
})

# Print the DataFrame
print("Metrics Before Tuning:")
print(metrics_df)


Metrics Before Tuning:
            Classifier  Precision    Recall  F1 Score  Accuracy
0          Naive Bayes   0.567378  0.609725  0.500177  0.534424
1    Gradient Boosting   0.860706  0.802727  0.827177  0.903204
2        Random Forest   0.849034  0.798387  0.820106  0.898432
3  K-Nearest Neighbors   0.725193  0.765059  0.741097  0.828221


In [58]:
# Metrics After Tuning
# Random Forest
accuracy_train_rf_tuned = accuracy_score(y_train_smote, best_rf_clf.predict(X_train_scaled))
accuracy_test_rf_tuned = accuracy_score(y_test, best_rf_clf.predict(X_test_scaled))
report_train_rf_tuned = classification_report(y_train_smote, best_rf_clf.predict(X_train_scaled), output_dict=True)
report_test_rf_tuned = classification_report(y_test, best_rf_clf.predict(X_test_scaled), output_dict=True)

# K-Nearest Neighbors
accuracy_train_knn_tuned = accuracy_score(y_train_smote, best_knn_clf.predict(X_train_scaled))
accuracy_test_knn_tuned = accuracy_score(y_test, best_knn_clf.predict(X_test_scaled))
report_train_knn_tuned = classification_report(y_train_smote, best_knn_clf.predict(X_train_scaled), output_dict=True)
report_test_knn_tuned = classification_report(y_test, best_knn_clf.predict(X_test_scaled), output_dict=True)

# Gradient Boosting
accuracy_train_gbm_tuned = accuracy_score(y_train_smote, best_gbm_clf.predict(X_train_scaled))
accuracy_test_gbm_tuned = accuracy_score(y_test, best_gbm_clf.predict(X_test_scaled))
report_train_gbm_tuned = classification_report(y_train_smote, best_gbm_clf.predict(X_train_scaled), output_dict=True)
report_test_gbm_tuned = classification_report(y_test, best_gbm_clf.predict(X_test_scaled), output_dict=True)

# Naive Bayes
accuracy_train_nb_tuned = accuracy_score(y_train_smote, best_nb_clf.predict(X_train_scaled))
accuracy_test_nb_tuned = accuracy_score(y_test, best_nb_clf.predict(X_test_scaled))
report_train_nb_tuned = classification_report(y_train_smote, best_nb_clf.predict(X_train_scaled), output_dict=True)
report_test_nb_tuned = classification_report(y_test, best_nb_clf.predict(X_test_scaled), output_dict=True)

# Compile the results into a dataframe
import pandas as pd

metrics_after_tuning = pd.DataFrame({
    "Classifier": ["Random Forest", "K-Nearest Neighbors", "Gradient Boosting", "Naive Bayes"],
    "Precision": [
        report_test_rf_tuned['macro avg']['precision'],
        report_test_knn_tuned['macro avg']['precision'],
        report_test_gbm_tuned['macro avg']['precision'],
        report_test_nb_tuned['macro avg']['precision']
    ],
    "Recall": [
        report_test_rf_tuned['macro avg']['recall'],
        report_test_knn_tuned['macro avg']['recall'],
        report_test_gbm_tuned['macro avg']['recall'],
        report_test_nb_tuned['macro avg']['recall']
    ],
    "F1 Score": [
        report_test_rf_tuned['macro avg']['f1-score'],
        report_test_knn_tuned['macro avg']['f1-score'],
        report_test_gbm_tuned['macro avg']['f1-score'],
        report_test_nb_tuned['macro avg']['f1-score']
    ],
    "Accuracy": [
        accuracy_test_rf_tuned,
        accuracy_test_knn_tuned,
        accuracy_test_gbm_tuned,
        accuracy_test_nb_tuned
    ]
})

print("Metrics After Tuning:")
print(metrics_after_tuning)


Metrics After Tuning:
            Classifier  Precision    Recall  F1 Score  Accuracy
0        Random Forest   0.849034  0.798387  0.820106  0.898432
1  K-Nearest Neighbors   0.725193  0.765059  0.741097  0.828221
2    Gradient Boosting   0.860706  0.802727  0.827177  0.903204
3          Naive Bayes   0.567378  0.609725  0.500177  0.534424


PLOTTING RESULT

In [63]:

# Model names
models = ['Naive Bayes', 'GBM', 'Random Forest', 'K-Nearest Neighbors (KNN)']

# Testing accuracies before tuning
accuracies_before_tuning = [accuracy_test_nb, accuracy_test_gbm, accuracy_test_rf, accuracy_test_knn]

# Testing accuracies after tuning
accuracies_after_tuning = [accuracy_test_nb_tuned, accuracy_test_gbm_tuned, accuracy_test_rf_tuned, accuracy_test_knn_tuned]

# Combine model names and accuracies
data_before_tuning = list(zip(models, accuracies_before_tuning))
data_after_tuning = list(zip(models, accuracies_after_tuning))

# Combine model names and both accuracies for sorting based on after tuning
combined_data = list(zip(models, accuracies_before_tuning, accuracies_after_tuning))

# Sort the combined data by accuracies after tuning (high to low)
combined_data.sort(key=lambda x: x[2], reverse=True)

# Unzip the sorted data
sorted_models, sorted_accuracies_before_tuning, sorted_accuracies_after_tuning = zip(*combined_data)

# Create figure
fig = go.Figure()

# Add bar trace for accuracies before tuning
fig.add_trace(go.Bar(
    x=sorted_models,
    y=sorted_accuracies_before_tuning,
    name='Before Tuning',
    marker_color='rgb(55, 83, 109)'
))

# Add bar trace for accuracies after tuning
fig.add_trace(go.Bar(
    x=sorted_models,
    y=sorted_accuracies_after_tuning,
    name='After Tuning',
    marker_color='rgb(26, 118, 255)'
))

# Update layout
fig.update_layout(
    title='Testing Accuracies Before and After Tuning (Sorted by After Tuning)',
    xaxis=dict(title='Model'),
    yaxis=dict(title='Accuracy', range=[0, 1]),
    barmode='group',
    bargap=0.15,
    bargroupgap=0.1 
)

# Show plot
fig.show()


In [65]:

# Model names
models = ['Naive Bayes', 'GBM', 'Random Forest', 'K-Nearest Neighbors (KNN)']

# Testing accuracies before tuning
accuracies_before_tuning = [accuracy_test_nb, accuracy_test_gbm, accuracy_test_rf, accuracy_test_knn]

# Testing accuracies after tuning
accuracies_after_tuning = [accuracy_test_nb_tuned, accuracy_test_gbm_tuned, accuracy_test_rf_tuned, accuracy_test_knn_tuned]

# Combine model names and accuracies
data_before_tuning = list(zip(models, accuracies_before_tuning))
data_after_tuning = list(zip(models, accuracies_after_tuning))

# Sort the data by accuracies (high to low)
data_before_tuning.sort(key=lambda x: x[1], reverse=True)
data_after_tuning.sort(key=lambda x: x[1], reverse=True)

# Unzip the sorted data
sorted_models_before_tuning, sorted_accuracies_before_tuning = zip(*data_before_tuning)
sorted_models_after_tuning, sorted_accuracies_after_tuning = zip(*data_after_tuning)

# Create figure
fig = go.Figure()

# Add bar trace for accuracies before tuning
fig.add_trace(go.Bar(
    x=sorted_models_before_tuning,
    y=sorted_accuracies_before_tuning,
    name='Before Tuning',
    marker_color='rgb(55, 83, 109)'
))

# Add bar trace for accuracies after tuning
fig.add_trace(go.Bar(
    x=sorted_models_after_tuning,
    y=sorted_accuracies_after_tuning,
    name='After Tuning',
    marker_color='rgb(26, 118, 255)'
))

# Update layout
fig.update_layout(
    title='Testing Accuracies Before and After Tuning (Sorted by Before Tuning)',
    xaxis=dict(title='Model'),
    yaxis=dict(title='Accuracy', range=[0, 1]),
    barmode='group',
    bargap=0.15,
    bargroupgap=0.1 
)

# Show plot
fig.show()
